In [2]:
import pandas as pd
import os
import get_chdir_signatures
import plotly.express as px
from sklearn.decomposition import PCA
import umap
from sklearn.manifold import TSNE

In [42]:
folder = "../data/LINCS_CFDE/GSE92742_full_batches"
pred_folder = "../data/LINCS_CFDE/L1000_GSE92742_prediction_results_step2_batch_divided_38_35"
gene_filename = folder+"/GSE92742_genes.txt"
inst_filename = "../data/L1000/GSE92742_Broad_LINCS_inst_info.txt"
pert_filename = "../data/L1000/GSE92742_Broad_LINCS_pert_info.txt"
gene_info_filename = "../data/L1000/GSE92742_Broad_LINCS_gene_info.txt"
l1000_folder = "../data/LINCS_CFDE/GSE92742_full_batches"
touchstone_filename = "../data/L1000/touchstone.txt"
signature_folder = "../data/L1000_signatures"
# cp_keywords = ["HDAC inhibitor", "Topoisomerase inhibitor", "CDK inhibitor", "ATPase inhibitor"]
cp_keywords = [
#     'Zinc fingers, C2H2-type',
#  'CD molecules',
#  'Dopamine receptor antagonist',
#  'GPCR / Class A : Orphans',
#  'RING-type (C3HC4) zinc fingers',
#  'RNA binding motif (RRM) containing',
#  'EF-hand domain containing',
#  'Endogenous ligands',
#  'Adrenergic receptor antagonist',
#  'Basic helix-loop-helix proteins',
#  'Cyclooxygenase inhibitor',
#  'WD repeat domain containing',
#  'Acetylcholine receptor antagonist',
#  'Serotonin receptor antagonist',
 'Glucocorticoid receptor agonist',
#  'Adrenergic receptor agonist',
#  'Mitochondrial respiratory chain complex / Complex I',
#  'EGFR inhibitor',
#  'basic leucine zipper proteins',
#  'Zinc fingers, PHD-type',
#  'Histamine receptor antagonist',
#  'Ankyrin repeat domain containing',
#  'Serotonin receptor agonist',
#  'Glutamate receptor antagonist',
#  'BTB/POZ domain containing',
#  'SH2 domain containing',
 'HDAC inhibitor',
#  'Homeoboxes / ANTP class : HOXL subclass',
#  'Phosphodiesterase inhibitor',
#  'Bacterial cell wall synthesis inhibitor',
#  'Calcium channel blocker',
#  'RNA polymerase subunits',
#  'Immunoglobulin superfamily / C1-set domain containing',
#  'Dopamine receptor agonist',
#  'ETS Transcription Factors',
#  'Pleckstrin homology (PH) domain containing',
#  'S ribosomal proteins',
#  'Tumour necrosis factor (TNF) receptor family',
#  'Proteasome (prosome, macropain) subunits',
#  'Estrogen receptor agonist',
#  'Interleukins and interleukin receptors',
 'ATPase inhibitor',
#  'Aldehyde dehydrogenases',
 'CDK inhibitor',
#  'Sodium channel blocker',
#  'Adhesion Class GPCRs',
#  'Forkhead boxes',
#  'General transcription factors',
#  'Ubiquitin-conjugating enzymes E2',
#  'Histone deacetylases'
 ]


In [43]:
touchstone = pd.read_csv(touchstone_filename, sep="\t")

In [44]:
# load inst info
inst_info = pd.read_csv(inst_filename, sep="\t")

# generate experiment column
inst_info["batch"] = inst_info["rna_plate"].replace(to_replace='_X[0-9]', value='', regex=True)
pert_id_to_moa_dict = dict(zip(touchstone["ID"], touchstone["MoA"]))
inst_info["MoA"] = inst_info["pert_id"].map(pert_id_to_moa_dict)
inst_info = inst_info.dropna()


/home/maayanlab/anaconda3/envs/python37/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3170: DtypeWarning:

Columns (7) have mixed types.Specify dtype option on import or set low_memory=False.



In [45]:
pert_info = pd.read_csv(pert_filename, sep="\t")

In [46]:
landmark_genes = pd.read_csv(gene_info_filename, sep="\t")
landmark_genes = landmark_genes[landmark_genes["pr_is_lm"]==1]["pr_gene_symbol"].tolist()

# Scatter Plots using DEG

In [47]:
l1000_diff_gex_list = list()
pred_rnaseq_diff_gex_list = list()
metadata_list = list()
colnames = list()

for cp_keyword in cp_keywords:
    cp_inst_info = inst_info[inst_info["MoA"]==cp_keyword]
    cp_inst_info["filename"] = cp_inst_info["batch"]+"_"+cp_inst_info["pert_id"]


    for filename in cp_inst_info["filename"].unique():
        l1000_filepath = f"{signature_folder}/{cp_keyword}/l1000_signature_{filename}.csv"
        pred_rnaseq_filepath = f"{signature_folder}/{cp_keyword}/predicted_rnaseq_signature_{filename}.csv"

        # load l1000 diff gex and pred rna-seq diff gex files
        if os.path.exists(l1000_filepath) == True:
            df = pd.read_csv(l1000_filepath, index_col=0)
            l1000_diff_gex_list.append(df)

            df = pd.read_csv(pred_rnaseq_filepath, index_col=0)
            pred_rnaseq_diff_gex_list.append(df)

            colnames.append("_".join([cp_keyword, filename]))
            # break        
    

ipykernel_launcher:8: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [48]:
meta_df = pd.DataFrame()
meta_df["index"] = colnames
meta_df["MoA"] = colnames
meta_df["MoA"] = meta_df["MoA"].str.split("_", n=0, expand=True)
meta_df = meta_df.set_index("index")

In [49]:
l1000_diff_gex_df = pd.concat(l1000_diff_gex_list, axis=1)
l1000_diff_gex_df.columns = colnames
l1000_diff_gex_df = l1000_diff_gex_df.T

pred_rnaseq_diff_gex_df = pd.concat(pred_rnaseq_diff_gex_list, axis=1)
pred_rnaseq_diff_gex_df.columns = colnames
pred_rnaseq_diff_gex_df = pred_rnaseq_diff_gex_df.T


In [85]:
# reducer = PCA(n_components=2)
# reducer = umap.UMAP(n_neighbors=50, metric='euclidean', n_components=2, min_dist=0.1)
reducer = TSNE(perplexity=30, metric='euclidean', n_jobs=-1, angle=0.2)
reduced_l1000_diff_gex = reducer.fit_transform(l1000_diff_gex_df)
reducer = TSNE(perplexity=30, metric='euclidean', n_jobs=-1, angle=0.2)
reduced_pred_rnaseq_diff_gex = reducer.fit_transform(pred_rnaseq_diff_gex_df)


In [86]:
reduced_l1000_diff_gex_df = pd.DataFrame(reduced_l1000_diff_gex)
reduced_l1000_diff_gex_df["index"] = meta_df.index.tolist()
reduced_pred_rnaseq_diff_gex_df = pd.DataFrame(reduced_pred_rnaseq_diff_gex)
reduced_pred_rnaseq_diff_gex_df["index"] = meta_df.index.tolist()

In [89]:
# px.scatter_3d(reduced_l1000_diff_gex_df, x=0, y=1, z=2, color=meta_df["MoA"], hover_name="index", width=800, height=400)
px.scatter(reduced_l1000_diff_gex_df, x=0, y=1, color=meta_df["MoA"], opacity=0.5, hover_name="index", width=1000, height=800, title="TSNE using DEG from original L1000")


In [90]:
# px.scatter_3d(reduced_pred_rnaseq_diff_gex_df, x=0, y=1, z=2, color=meta_df["MoA"], hover_name="index", width=800, height=400)
px.scatter(reduced_pred_rnaseq_diff_gex_df, x=0, y=1, color=meta_df["MoA"], opacity=0.5, hover_name="index", width=1000, height=800, title="TSNE using DEG from predicted RNA-seq")


### only landmark genes

In [145]:
common_landmark_genes = set(pred_rnaseq_diff_gex_df.columns).intersection(pred_rnaseq_diff_gex_df)

In [146]:
reducer = PCA(n_components=2)
# reducer = umap.UMAP()
reduced_l1000_diff_gex = reducer.fit_transform(l1000_diff_gex_df[common_landmark_genes])
reduced_pred_rnaseq_diff_gex = reducer.fit_transform(pred_rnaseq_diff_gex_df[common_landmark_genes])


In [147]:
reduced_l1000_diff_gex_df = pd.DataFrame(reduced_l1000_diff_gex)
reduced_l1000_diff_gex_df["index"] = meta_df.index.tolist()
reduced_pred_rnaseq_diff_gex_df = pd.DataFrame(reduced_pred_rnaseq_diff_gex)
reduced_pred_rnaseq_diff_gex_df["index"] = meta_df.index.tolist()

In [148]:
px.scatter(reduced_l1000_diff_gex_df, x=0, y=1, color=meta_df["MoA"], hover_name="index", width=800, height=400)


In [149]:
px.scatter(reduced_pred_rnaseq_diff_gex_df, x=0, y=1, color=meta_df["MoA"], hover_name="index", width=800, height=400)


In [338]:
cp_gex_list = list()
i = 0
batch_ids = set(cp_inst_info["batch"].unique())
for batch in batch_ids:
    
    print(batch, i, "out of", len(batch_ids))
    try:
        batch_gex = get_chdir_signatures.load_feather(f"{pred_folder}/{batch}.f")
    except:
        continue
    cp_gex_list.append(batch_gex.loc[cp_inst_info.loc[cp_inst_info["batch"]==batch, "inst_id"], :])
    i +=1


    

CPC006_U937_6H 0 out of 626
DOS044_A375_24H 1 out of 626
DOS046_A549_24H 2 out of 626
CPC008_VCAP_24H 3 out of 626
DEB001_PC3_24H.A2 4 out of 626
CPC009_HCC515_6H 4 out of 626
CPC005_VCAP_6H 5 out of 626
CPC014_ASC_24H 6 out of 626
HOG003_MCF7_6H 7 out of 626
DOS055_MCF7_24H 8 out of 626
CPC016_MCF7_6H 9 out of 626
CPC006_SNUC5_6H 10 out of 626
CPC003_PC3_24H 11 out of 626
CPC006_RMGI_6H 12 out of 626
DOSBIO001_HT29_24H 13 out of 626
ERG005_VCAP_6H 14 out of 626
CPC002_VCAP_6H 15 out of 626
DOS019_VCAP_6H 16 out of 626
BRAF001_A375_6H 17 out of 626
CPC007_A549_6H 18 out of 626
CPC005_A375_6H 19 out of 626
CPC006_WSUDLCL2_6H 20 out of 626
CPD003_MCF7_6H 21 out of 626
HOG002_A549_6H 22 out of 626
CPC012_PC3_24H.L2 23 out of 626
CPC009_HT29_6H 23 out of 626
CPC011_MCF7_6H 24 out of 626
CPC007_PC3_24H 25 out of 626
ERG006_VCAP_24H 26 out of 626
CPC016_A549_6H 27 out of 626
CPC012_NPC_24H 28 out of 626
CPC009_MCF7_24H 29 out of 626
CPC013_A549_24H 30 out of 626
DOS004_VCAP_6H 31 out of 626


In [339]:
cp_gex_df = pd.concat(cp_gex_list)

In [361]:
cp_meta_df = pd.DataFrame(cp_gex_df.index)
cp_meta_df.columns = ['inst_id']
cp_meta_df = cp_meta_df.set_index("inst_id")
# inst_info = inst_info.set_index("inst_id")
cp_meta_df = cp_meta_df.join(inst_info)


In [354]:
#quantile normalization
from maayanlab_bioinformatics.normalization.quantile import quantile_normalize
all_gex_df_quantilenorm = quantile_normalize(cp_gex_df.T).T

KeyboardInterrupt: 

In [357]:
# pca = PCA(n_components=2)
# pca_batch_gex = pca.fit_transform(all_gex_df_quantilenorm)

pca = umap.UMAP()
pca_batch_gex = pca.fit_transform(cp_gex_df)


In [362]:
df = pd.DataFrame(pca_batch_gex)
df["index"] = cp_meta_df.index.tolist()

In [365]:
px.scatter(df, x=0, y=1, color=cp_meta_df["MoA"], hover_name="index", width=1200, height=800)


In [ ]:
batch = "CPC004_A375_6H"

batch_info = inst_info[inst_info["batch"]==batch].sort_values("inst_id")
batch_gex = get_chdir_signatures.load_feather(f"{pred_folder}/{batch}.f")

touchstone_pert_id_in_batch = [x for x in batch_info["pert_id"].unique() if pert_info.loc[pert_info["pert_id"] == x, "is_touchstone"].tolist()[0]==1 ]
touchstone_batch_info = batch_info[batch_info["pert_id"].isin(touchstone_pert_id_in_batch)]
touchstone_batch_gex = batch_gex.loc[touchstone_batch_info["inst_id"], :]

# Differentially Expressed Genes for each batch

In [320]:
batch = "CPC004_VCAP_24H"
# batch = "CPC006_PC3_6H"


batch_info = inst_info[inst_info["batch"]==batch].sort_values("inst_id")
# batch_gex = pd.read_csv(f"{signature_folder}/predicted_rnaseq_signature_{batch}.csv", index_col=0).T
batch_gex = pd.read_csv(f"{signature_folder}/l1000_signature_{batch}.csv", index_col=0).T
touchstone_pert_id_in_batch = [x for x in batch_info["pert_id"].unique() if pert_info.loc[pert_info["pert_id"] == x, "is_touchstone"].tolist()[0]==1 ]
touchstone_batch_info = batch_info[batch_info["pert_id"].isin(touchstone_pert_id_in_batch)]
touchstone_batch_gex = batch_gex.loc[touchstone_pert_id_in_batch, :]

In [321]:
touchstone_batch_gex[touchstone_batch_gex>0]=1
touchstone_batch_gex[touchstone_batch_gex<0]=0

In [322]:
pca = umap.UMAP(min_dist=0.1, n_neighbors=5, metric='jaccard')
# pca = TSNE()
# batch_gex_quantilenorm = quantile_normalize(touchstone_batch_gex.T).T
pca_batch_gex = pca.fit_transform(touchstone_batch_gex)




/home/maayanlab/anaconda3/envs/python37/lib/python3.7/site-packages/umap/umap_.py:1762: UserWarning:

gradient function is not yet implemented for jaccard distance metric; inverse_transform will be unavailable



In [323]:
touchstone_batch_gex

NMRK1  LRRC41  GFI1B  QPCT  SPHK1  HMGB1  DRD1  FGF9  GALNT14  \
BRD-A19500257    0.0     0.0    0.0   0.0    1.0    0.0   0.0   0.0      0.0   
BRD-A62184259    1.0     1.0    1.0   0.0    0.0    0.0   1.0   0.0      1.0   
BRD-K08109516    1.0     0.0    1.0   0.0    0.0    0.0   1.0   0.0      0.0   
BRD-A11678676    0.0     1.0    0.0   1.0    0.0    1.0   0.0   1.0      0.0   
BRD-A09472452    0.0     1.0    0.0   1.0    0.0    1.0   1.0   1.0      1.0   
...              ...     ...    ...   ...    ...    ...   ...   ...      ...   
BRD-K30867024    1.0     0.0    1.0   1.0    0.0    1.0   0.0   1.0      0.0   
BRD-K98490050    0.0     0.0    1.0   1.0    1.0    1.0   1.0   0.0      1.0   
BRD-A48237631    0.0     0.0    0.0   1.0    1.0    1.0   0.0   0.0      1.0   
BRD-K81418486    0.0     0.0    0.0   1.0    0.0    0.0   0.0   1.0      1.0   
BRD-K43389675    0.0     0.0    1.0   1.0    1.0    1.0   1.0   0.0      1.0   

               RHOG  ...  NTF3  CFAP69  PARP3  PLEKHA6  SLC9A8  TBC1D13  \
BRD-A19500257   1.0  ...   0.0     1.0    0.0      1.0     0.0      1.0   
BRD-A62184259   1.0  ...   1.0     1.0    0.0      1.0     0.0      1.0   
BRD-K08109516   1.0  ...   1.0     1.0    0.0      1.0     0.0      1.0   
BRD-A11678676   1.0  ...   0.0     1.0    1.0      1.0     1.0      0.0   
BRD-A09472452   1.0  ...   1.0     1.0    0.0      1.0     0.0      0.0   
...             ...  ...   ...     ...    ...      ...     ...      ...   
BRD-K30867024   1.0  ...   0.0     0.0    0.0      0.0     1.0      1.0   
BRD-K98490050   0.0  ...   0.0     1.0    1.0      1.0     0.0      0.0   
BRD-A48237631   1.0  ...   0.0     1.0    1.0      1.0     0.0      0.0   
BRD-K81418486   0.0  ...   0.0     1.0    1.0      0.0     1.0      1.0   
BRD-K43389675   1.0  ...   1.0     0.0    0.0      1.0     0.0      0.0   

               SERPINI2  NBEA  MUTYH  GMPPA  
BRD-A19500257       0.0   0.0    1.0    1.0  
BRD-A62184259       0.0   0.0    1.0    1.0  
BRD-K08109516       0.0   0.0    0.0    1.0  
BRD-A11678676       1.0   0.0    0.0    0.0  
BRD-A09472452       0.0   1.0    1.0    0.0  
...                 ...   ...    ...    ...  
BRD-K30867024       0.0   1.0    1.0    1.0  
BRD-K98490050       1.0   0.0    1.0    1.0  
BRD-A48237631       1.0   1.0    0.0    0.0  
BRD-K81418486       1.0   1.0    0.0    0.0  
BRD-K43389675       0.0   0.0    1.0    0.0  

[311 rows x 11833 columns]

In [324]:
df = pd.DataFrame(pca_batch_gex)

df["index"] = touchstone_batch_gex.index.tolist()
df["pert_id"]=touchstone_batch_gex.index.tolist()
df["MoA"] = [pert_id_to_moa_dict[x] for x in touchstone_batch_gex.index]
df = df.sort_values("MoA")

In [325]:
px.scatter(df, x=0, y=1, color=df["MoA"],
                 width=1800, height=800, hover_name="pert_id")
